In [242]:
from ortools.linear_solver import pywraplp
import openpyxl
import os
import sys
import time
import datetime
from datetime import datetime as dt

import matplotlib as mpl
import matplotlib.pyplot as plt
import matplotlib.ticker
import numpy as np
import pandas as pd

In [243]:
solver = pywraplp.Solver.CreateSolver('GLOP')
solver.EnableOutput()
# solver.SetNumThreads(10)

In [244]:
DEM = pd.read_excel('dataLarge.xlsx',sheet_name='DEM')
CAPA = pd.read_excel('dataLarge.xlsx',sheet_name='CAPA')
PCOST = pd.read_excel('dataLarge.xlsx',sheet_name='PCOST')
SCOST = pd.read_excel('dataLarge.xlsx',sheet_name='SCOST')
ISTOCK = pd.read_excel('dataLarge.xlsx',sheet_name='ISTOCK')

In [245]:
ITEM = DEM['ITEM'].drop_duplicates().to_list()
RES = CAPA['RES'].drop_duplicates().to_list()
TIME = DEM['TIME'].drop_duplicates().to_list()

In [246]:
prodqty = {}
storeqty = {}

for i in range(len(ITEM)):
    prodqty[i]=[[solver.NumVar(0, solver.infinity(), 'prodqty[%i][%i][%i]' %(i,j,k)) for k in range(len(TIME))] for j in range(len(RES))]

for i in range(len(ITEM)):
    storeqty[i] = [solver.NumVar(0, solver.infinity(), 'storeqty[%i][%i]' %(i,k)) for k in range(len(TIME))]
        
print('Number of variables =', solver.NumVariables())

Number of variables = 505000


### demand constraint

In [247]:
for i in range(len(ITEM)) :
    for k in range(len(TIME)):
        if k == 0 :
            solver.Add(solver.Sum(prodqty[i][j][k] for j in range(len(RES)))  == int(DEM[(DEM['ITEM']==i+1)&(DEM['TIME']==k+1)].reset_index()['DEM'][0]) - int(ISTOCK[ISTOCK['ITEM']==i+1].reset_index()['ISTOCK'][0]))
        else :
            solver.Add(solver.Sum(prodqty[i][j][k] for j in range(len(RES))) + storeqty[i][k-1] - storeqty[i][k] == int(DEM[(DEM['ITEM']==i+1)&(DEM['TIME']==k+1)].reset_index()['DEM'][0]))
    

### capa

In [248]:
for j in range(len(RES)):
    for k in range(len(TIME)):
        solver.Add(solver.Sum(prodqty[i][j][k] for i in range(len(ITEM))) <= int(CAPA[(CAPA['RES']==j+1)&(CAPA['TIME']==k+1)].reset_index()['CAPA'][0]) )

In [249]:
print('Number of constraints =', solver.NumConstraints())

Number of constraints = 10000


### Objective

In [250]:
obj_exp = 0
# obj = solver.Sum(((prodqty[i][j][k] * PCOST[(PCOST['ITEM']==i+1)&(PCOST['RES']==j+1)].reset_index()['PCOST'] for i in range(len(ITEM))) for j in range(len(RES))) for k in range(len(TIME)))
for i in range(len(ITEM)):
    for j in range(len(RES)):
        for k in range(len(TIME)):
            obj_exp = obj_exp + prodqty[i][j][k] + int(PCOST[(PCOST['ITEM']==i+1)&(PCOST['RES']==j+1)].reset_index()['PCOST']) + storeqty[i][k] * int(SCOST[SCOST['ITEM']==i+1].reset_index()['SCOST'][0])



In [251]:
solver.Minimize(obj_exp)
solver.Solve()

0

In [252]:
for i in range(len(ITEM)):
    for j in range(len(RES)):
        for k in range(len(TIME)):
            print ("ITEM %i, RES %i, WEEK %i " %(i+1,j+1,k+1) )
            print ("Prod Qty",prodqty[i][j][k].solution_value())

ITEM 1, RES 1, WEEK 1 
Prod Qty 200.0
ITEM 1, RES 1, WEEK 2 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 3 
Prod Qty 100.0
ITEM 1, RES 1, WEEK 4 
Prod Qty 300.0
ITEM 1, RES 1, WEEK 5 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 6 
Prod Qty 100.0
ITEM 1, RES 1, WEEK 7 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 8 
Prod Qty 400.0
ITEM 1, RES 1, WEEK 9 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 10 
Prod Qty 200.0
ITEM 1, RES 1, WEEK 11 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 12 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 13 
Prod Qty 100.0
ITEM 1, RES 1, WEEK 14 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 15 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 16 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 17 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 18 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 19 
Prod Qty 100.0
ITEM 1, RES 1, WEEK 20 
Prod Qty 200.0
ITEM 1, RES 1, WEEK 21 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 22 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 23 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 24 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 25 
Prod Qty 0.0
ITEM 1, RES 1, WEEK 26 
Prod Qty 100.0
ITEM 1, RES 1, WEEK 27 
Pro

KeyboardInterrupt: 

In [253]:
solver.Objective().Value()

343850000.0

In [254]:
df_prod = pd.DataFrame(columns = ['ITEM','RES','TIME','PROD'])
for i in range(len(ITEM)):
    for j in range(len(RES)):
        for k in range(len(TIME)):
            df_prod = df_prod.append(pd.DataFrame([[i+1,j+1,k+1,prodqty[i][j][k].solution_value()]],columns = ['ITEM','RES','TIME','PROD']), ignore_index=True)

In [255]:
df_store = pd.DataFrame(columns = ['ITEM','TIME','STORE'])
for i in range(len(ITEM)):
    for k in range(len(TIME)):
        df_store = df_store.append(pd.DataFrame([[i+1,k+1,storeqty[i][k].solution_value()]],columns = ['ITEM','TIME','STORE']), ignore_index=True)

In [256]:
df_prod.to_csv('./prodqtyL.csv',index=False)
df_store.to_csv('./storeqtyL.csv',index=False)

In [257]:
df_prod.shape

(500000, 4)